In [5]:
import json
import re
from pprint import pprint

import numpy as np
import pandas as pd
from IPython.core.display import HTML, display
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.compose import ColumnTransformer
from sklearn.dummy import DummyClassifier
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.pipeline import Pipeline
from sklearn import svm
import spacy

nlp = spacy.load('ru_core_news_md')



/tmp/ipykernel_99851/222207882.py:7: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import HTML, display


In [6]:


class FullDescriptionCreator(BaseEstimator, TransformerMixin):
    patt = re.compile("[^\s\w]")

    def __init__(self, responsibilities):
        self.responsibilities = responsibilities

    def fit(self, X, y=None):
        return self

    def transform(self, X):
        X = X.copy()
        X["responsibilities"] = self.responsibilities
        X["full_description"] = (
            X["name"] + " " + X["responsibilities"].fillna("")
        ).map(str.lower)
        X.loc[:, "full_description"] = X["full_description"].str.replace(
            self.patt, " ", regex=True
        )
        return X


train = pd.read_csv("./train.csv", index_col="index")
print(f"{train.shape}")
print("Типы столбцов: ")
display(train.dtypes)
print("Фрагмент данных: ")
display(train.head())


(30000, 3)
Типы столбцов: 


name           object
description    object
target          int64
dtype: object

Фрагмент данных: 


name  \
index                                                          
324865089                                    продавец кассир   
169467135                        продавец мила (шевченко 17)   
169939030                        кассир в пиццерию г витебск   
31956044                     начальник строительного участка   
36781653   продавец кассир (санкт петербург бухарестская 31)   

                                                 description  target  
index                                                                 
324865089  <strong>Обязанности:</strong> <ul> <li>работа ...      -1  
169467135  <p><strong>Магазин МИЛА по адресу б-р Шевченко...      -1  
169939030  <p><strong>Устал искать работу? Может, хочешь ...    5223  
31956044   <p>Компании &quot;Артель-Строй&quot; на постоя...      -1  
36781653   <p>Обязанности:</p><p>    •Обслуживание покупа...      -1

In [7]:

train = train.query("target != -1")
print(f"{train.shape=}")

train.at[169939030, "description"]

with open(
    "./vacancy_descriptions/2_parsed.json", "r", encoding="utf8"
) as fp:
    descriptions = json.load(fp)
    

responsibilities = pd.Series({
    description["ID"]: r[0]
    if (r := description["Content"].get("Обязанности")) is not None
    else None
    for description in descriptions
}, name="responsibilities")


train["responsibilities"] = responsibilities

train["full_description"] = (
    train["name"] + " " + train["responsibilities"].fillna("")
).map(str.lower)

patt = re.compile("[^\w\s]")
train.loc[:, "full_description"] = train["full_description"].str.replace(
    patt, " ", regex=True
)

X_train_raw, y_train = train["full_description"], train["target"]

X_train_raw


docs = [nlp(text) for text in X_train_raw]
train_x_word_vectors = [x.vector for x in docs]

train_x_word_vectors


train.shape=(15000, 3)


[array([ 3.99117284e-02, -9.82181206e-02,  4.97139581e-02, -5.91704734e-02,
         1.01846442e-01, -3.11879418e-03,  5.65807298e-02,  7.84928910e-03,
         5.63152842e-02,  1.35749206e-01, -1.04826830e-01, -5.08029275e-02,
         3.36669609e-02, -3.10785975e-02, -3.94849516e-02, -5.28261140e-02,
        -4.69390564e-02,  1.21605908e-02, -1.64857749e-02,  1.15112834e-01,
        -2.54863080e-05, -8.69646892e-02, -1.03769556e-01,  1.45180076e-02,
         1.09936595e-02,  9.14914832e-02, -1.29455160e-02,  2.06042513e-01,
         2.98964661e-02, -1.63145475e-02, -9.58114490e-02, -9.20791551e-02,
         1.97015002e-01, -1.24417841e-01, -4.44231704e-02, -1.02948323e-01,
         1.25867054e-02, -5.67673966e-02, -8.99263024e-02, -7.99729824e-02,
        -1.29972562e-01, -1.09937200e-02,  8.11358765e-02, -2.04042792e-02,
        -7.76564553e-02,  2.39120703e-02,  1.40916007e-02, -9.28021073e-02,
        -1.94081683e-02, -4.14131396e-02, -2.82740500e-02, -1.19084634e-01,
        -6.7

In [8]:
clf_svm_wv = svm.SVC(kernel='linear')
clf_svm_wv.fit(train_x_word_vectors, y_train)

SVC(kernel='linear')

In [17]:
print(clf_svm_wv.predict(train_x_word_vectors[4].reshape(1,-1)))
y_train

[6121]


index
169939030    5223
169293782    5223
291073919    7212
179260831    5223
39608878     6121
             ... 
110663394    3341
30812168     3341
50002587     3341
183546781    3341
39324585     6121
Name: target, Length: 15000, dtype: int64